In [1]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as anm
import matplotlib.gridspec as gridspec
import matplotlib.animation as anim

In [2]:
class house:
    def __init__(self, dimensions, h_t, T, f, diff_coeff, border_indexes, radiators_indexes, doors_indexes, windows_indexes, inside_temp, outside_temp):
        self.windows = windows_indexes
        self.h_t = h_t
        self.T = T
        self.t = np.arange(0, self.T+self.h_t, self.h_t)
        self.f = f
        self.diff_coeff = diff_coeff
        self.doors = doors_indexes
        self.radiators = list(radiators_indexes.values())
        self.dimensions = dimensions
        self.border_indexes = border_indexes
        self.matrix = np.zeros((len(self.t),)+ self.dimensions)
        self.rooms = []
        self.inside_t = inside_temp
        self.outside_t = outside_temp
        self.total_energy = list(np.arange(0, self.T+self.h_t, self.h_t)*0)
        for number, room in self.border_indexes.items():
            self.matrix[:, min(list(zip(*room))[0]):max(list(zip(*room))[0]), min(list(zip(*room))[1]):max(list(zip(*room))[1])] = self.inside_t 
            self.rooms.append(self.matrix[:, min(list(zip(*room))[0]):max(list(zip(*room))[0]), min(list(zip(*room))[1]):max(list(zip(*room))[1])].view())
    def welcome(self):
        plt.imshow(self.matrix[0,:,:])
        plt.title("House area")
    def calculate(self):
        h_x = 1
        for j in np.arange(1,len(self.t),1): 
            for k in range(len(self.border_indexes)): 
                self.rooms[k][j, 1:-1 , 1:-1] = self.rooms[k][j-1, 1:-1 , 1:-1] + self.diff_coeff*self.h_t/h_x**2*(self.rooms[k][j-1, 2:, 1:-1] + self.rooms[k][j-1, 0:-2, 1:-1] + self.rooms[k][j-1, 1:-1, 2:] + self.rooms[k][j-1, 1:-1, 0:-2]-4*self.rooms[k][j-1, 1:-1 , 1:-1])
                self.rooms[k][j, -1 , :] = self.rooms[k][j, -2 , :]
                self.rooms[k][j, 0 , :] = self.rooms[k][j, 1 , :]
                self.rooms[k][j, : , -1] = self.rooms[k][j, : , -2]
                self.rooms[k][j, : , 0] = self.rooms[k][j, : , 1] 
                for l in self.radiators[k]: 
                    try:
                        if np.mean(self.rooms[k][j-1, : , :]) <= l[2]:
                            self.matrix[j, l[0] , l[1]] += self.h_t*self.f
                            self.total_energy[j] +=self.h_t*self.f
                    except IndexError:
                        pass
            for m in self.doors:
                self.matrix[j, m[0] , m[1]] = self.matrix[j-1, m[0] , m[1]] + self.diff_coeff*self.h_t/h_x**2*(self.matrix[j-1, m[0]+1, m[1]] + self.matrix[j-1, m[0]-1, m[1]] + self.matrix[j-1, m[0], m[1]+1] + self.matrix[j-1, m[0], m[1]-1]-4*self.matrix[j-1, m[0] , m[1]])
            for n in self.windows:
                self.matrix[j, n[0] , n[1]] = self.outside_t        
        return self.matrix
    def animate(self, anim_step=60):
        solution = self.calculate()[0::anim_step, :, :]-273
        t_cp = self.t[anim_step::]
        x = np.arange(0, np.shape(solution)[2], 1)
        y = np.arange(0, np.shape(solution)[1], 1)
        fig = plt.figure(figsize=(5, 5), facecolor='white')
        gs = gridspec.GridSpec(1, 1)
        ax1 = plt.subplot(gs[0, 0])
        ax1.set_xlim((np.min(x), np.max(x)))
        ax1.set_ylim((np.max(y), np.min(y)))
        ax1.set_xlabel("$x$")
        ax1.set_ylabel("$y$")
        pcolormesh_d = ax1.pcolormesh(x, y, solution[0,:,:], shading='gouraud',vmin=0, vmax=30)
        cb1 = fig.colorbar(pcolormesh_d,ax=ax1)
        def animation(j):
            pcolormesh_d.set_array(solution[j,:, :].ravel())
            ax1.set_title("Time: {:.2f} minutes".format(j * anim_step * self.h_t/ 60))
            return pcolormesh_d

        anim = anm.FuncAnimation(fig,
                         func = animation,
                         frames = solution.shape[0],
                         interval = 100,
                         blit = False
                         )
        plt.close()
        plt.rc('animation', html='jshtml')
        return anim


In [3]:
borders = {
    1 : [(0, 0), (0,15), (10,15), (10,0)], 
    2 : [(10, 0), (10,15), (22,15), (22,0)],
    3 : [(22, 0), (22,15), (30,15), (30,0)],
    4 : [(0, 15), (0,18), (30,18), (30,15)],
    5 : [(0, 18), (0,30), (15,18), (15,30)],
}

radiators = {
    1 : [(5, 1, 273+19), (1,6, 273+19)], #(y, x, max_temperature)
    2 : [(15, 1, 273+19)],
    3 : [(25, 1, 273+19)],
    4 : [],
    5 : [(8, 28, 273+22), (1,25, 273+22), (13, 25,273+22)],
}

doors = [(5,14),(5,15), (15,14),(15,15), (25,14),(25,15), (9,6),(10,6), (21,6),(22,6), (5,17),(5,18)]
windows = [(5,0), (15,0), (25,0), (29,6), (0,6), (0,25), (8,29)]


a = house(dimensions = (30,30), h_t = 1, T=60*180, f=0.5, diff_coeff=0.01, border_indexes = borders,
          radiators_indexes = radiators, doors_indexes = doors, windows_indexes = windows,
          inside_temp=286, outside_temp=278)


a.animate(anim_step=180)